In [173]:
!pip install selenium

In [45]:
import pandas as pd
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import bs4
import requests
import time

In [125]:
#เปิดเว็บ Sanook
driver = webdriver.Chrome()
driver.get('https://www.sanook.com/news/')

In [126]:
# ค้นหาช่องค้นหา
search = driver.find_element("xpath",'/html/body/div[2]/div[1]/header/div/div/div[2]/div/form/label/input')

In [127]:
# พิมพ์คำว่า การศึกษาไทย
search.send_keys('การศึกษาไทย')

In [128]:
# กดค้นหา
search.send_keys(Keys.ENTER)

In [129]:
driver.execute_script("document.body.style.zoom='100%'")

# Scraping

In [130]:
# INFINITE scrolling pages
# เลื่อนลงเพื่อให้โหลดข่าวเยอะๆ

previous_height = driver.execute_script('return document.body.scrollHeight')

for i in range(2):
    while True:
        driver.execute_script('window.scrollTo(0,  document.body.scrollHeight);')

        time.sleep(3)

        new_height = driver.execute_script('return document.body.scrollHeight')

        if new_height == previous_height:
            break
        previous_height = new_height
        

In [131]:
data = driver.page_source
soup = bs4.BeautifulSoup(data)

In [132]:
# เก็บลิ้งค์ข่าวทั้งหมดในหน้า 
links = []
for link_news in soup.findAll('span',{'class':'jsx-2430232205 jsx-2715185928 text-color-news'}):
    links.append(link_news.a['href'])
print(len(links))

152


In [133]:
all_links = []
Title = []
Release_date = [] 
Contents = []

order = 1

a = 1
# เข้าไปทีละข่าว
for link in links:
    
    print(link)
    #time.sleep(3)
    page = requests.get(link , allow_redirects=False)
    content_news = bs4.BeautifulSoup(page.content , "lxml")
    a += 1
    #content_news = bs4.BeautifulSoup(page.content , "lxml")
    
    for e in content_news('body') :
        # หาชื่อข่าว
        title=e.find('div', attrs={'class':'jsx-223461968 EntryHeading clearfix'}).find('h1' , {'class' : 'jsx-223461968 title'}).text
        # หาวันที่เผยแพร่
        release_date=e.find('span',attrs={'class':'jsx-1665670616 infoItem'}).time['datetime']
        # หาเนื้อข่าวทั้งหมด
        #Contents = e.find('div',attrs={'id':'EntryReader_0'}).get_text(strip=True)
        Contents.append(e.find('div',attrs={'id':'EntryReader_0'}).get_text(strip=True))
        
        # เพิ่มเข้าไปใน list
        all_links.append(link)
        Title.append(title)
        Release_date.append(release_date)
        print(f'{order} {link} : {title}')
        print(f'Date : {release_date}')
        
        order += 1

https://www.sanook.com/news/8650938/
1 https://www.sanook.com/news/8650938/ : “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย
Date : 2022-11-07 18:21
https://www.sanook.com/news/8637914/
2 https://www.sanook.com/news/8637914/ : “กระทรวงศึกษาธิการ” ปลดล็อกการศึกษาไทย ด้วยนโยบาย “ซ่อม สร้าง ป้องกัน”
Date : 2022-10-11 17:31
https://www.sanook.com/news/8614190/
3 https://www.sanook.com/news/8614190/ : “ภาวะการเรียนรู้ถดถอย” ภัยเงียบที่กำลังกัดเซาะสังคม
Date : 2022-08-26 17:50
https://www.sanook.com/news/8602854/
4 https://www.sanook.com/news/8602854/ : ครูจุ๊ย กุลธิดา: เปลือยการศึกษาไทยช่วงวิกฤติโควิด-19
Date : 2022-08-04 15:44
https://www.sanook.com/news/8588214/
5 https://www.sanook.com/news/8588214/ : 2 เยาวชนไทยในโอลิมปิกปรัชญาและเหรียญทองแดงแรกในประวัติศาสตร์
Date : 2022-07-06 16:20
https://www.sanook.com/news/8569186/
6 https://www.sanook.com/news/8569186/ : นพ.ยงยุทธ วงศ์ภิรมย์ศานติ์: จิตวิทยาว่าด้วย “ความงมงาย” ของคนไทย
Date : 2022-05-30 13:10
https://www.sanook.com/

In [134]:
import pandas as pd

In [135]:
df = {'Title': Title,
        'Release_date':Release_date,
        'Content':Contents,
        }
# Create Data Frame
df = pd.DataFrame(df)
df

Title      Release_date  \
0    “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
1    “กระทรวงศึกษาธิการ” ปลดล็อกการศึกษาไทย ด้วยนโย...  2022-10-11 17:31   
2    “ภาวะการเรียนรู้ถดถอย” ภัยเงียบที่กำลังกัดเซาะ...  2022-08-26 17:50   
3    ครูจุ๊ย กุลธิดา: เปลือยการศึกษาไทยช่วงวิกฤติโค...  2022-08-04 15:44   
4    2 เยาวชนไทยในโอลิมปิกปรัชญาและเหรียญทองแดงแรกใ...  2022-07-06 16:20   
..                                                 ...               ...   
147        พล.อ.สุรยุทธ์เผย ในหลวงทรงห่วงใยการศึกษาไทย  2013-07-25 13:03   
148            ฮือฮา! เด็ก 2 ขวบ อัจฉริยะภาษา (ชมคลิป)  2013-07-13 13:53   
149          ดุสิตโพลคนฝากรมต.ใหม่เร่งแก้ใต้กระตุ้นศก.  2013-07-05 11:23   
150           Sanook social news วันที่ 5 กรกฎาคม 2556  2013-07-05 10:15   
151              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   

                                               Content  
0    Highlightรายงานฉบับพิเศษ “ห้องเรียนฟื้นฟูหลังโ...  
1    การศึกษาของเด็กไทยคือหัวใจสำคัญในการขับเคลื่อน...  
2    Highlightบทเรียนงานวิจัยเกี่ยวกับพัฒนาการเด็กป...  
3    Highlightระบบราชการ ระบบคิดของคนต่อการศึกษา แล...  
4    ชวนรู้จักกับ 2 เยาวชนไทยที่คว้าเหรียญทองแดงและ...  
..                                                 ...  
147  องคมนตรี สุรยุทธ์ เผย พระบาทสมเด็จพระเจ้าอยู่ห...  
148  วันที่ 11 ก.ค. ผู้สื่อข่าวรับแจ้งมีเด็กอัจริยะ...  
149  ดุสิตโพล เผย ประชาชนอยากฝากรัฐมนตรีใหม่ เร่งแก...  
150  คัดเรื่องเด่นประเด็นฮอตในรอบสัปดาห์กับSanook! ...  
151  ปลัดกระทรวงศึกษาธิการ แจง กรรมาธิการงบประมาณปี...  

[152 rows x 3 columns]

In [108]:
# Change Data type DATE to datetime
from datetime import datetime
df['Release_date'] = pd.to_datetime(df['Release_date'])

In [109]:
# Check DataType
df.dtypes

Title                   object
Release_date    datetime64[ns]
Content                 object
dtype: object

In [113]:
# ลบพวกตัวแปลกๆ \xa0 , \u200b
df['Content']= df['Content'].replace(to_replace='\xa0', regex=True, value='')
df['Content']= df['Content'].replace(to_replace='\u200b', regex=True, value='')

In [114]:
df['Content'][0]

'เครือซีพีสนับสนุนภาคการศึกษาไทย มอบทุนการศึกษาต่อเนื่อง 41 ปีช่วยเยาวชนขาดแคลนทุนทรัพย์ หวังลดความเหลื่อมล้ำทางสังคม ปีนี้เดินหน้ามอบแก่นิสิตนักศึกษาทั่วประเทศ 262 ทุน ๆ ละ 30,000 บาทพร้อมอัดฉีดเรียนฟรี E Learning ตลอดช่วงรับทุน จากโรงเรียนสอนภาษาระดับโลกเสริมทักษะภาษาอังกฤษให้แข็งแกร่งรองรับเป็นศูนย์กลางอาเซียน ทั้งยังประกาศเพิ่มทุนการศึกษาด้านนวัตกรรมแก่นักเรียนม.ปลายและสายอาชีพเพื่อตอบโจทย์ไทยแลนด์ 4.0 สร้างคนเพื่อขับเคลื่อนประเทศด้วยนวัตกรรม31 พฤษภาคม 2562 – เครือเจริญโภคภัณฑ์ (ซีพี) จัดพิธีมอบทุนการศึกษาประจำปี 2562 แก่นิสิตนักศึกษาทั่วประเทศต่อเนื่องเป็นปีที่ 41 ถือเป็นทุนการศึกษาของภาคเอกชนที่มีประวัติศาสตร์ยาวนานที่สุดทุนหนึ่งของประเทศไทยโดยมีศาสตราจารย์เกียรติคุณ นพ.เกษม วัฒนชัยประธานคณะกรรมการบริหารทุนการศึกษา เครือเจริญโภคภัณฑ์ เป็นประธานมอบทุนการศึกษาฯ พร้อมด้วยนายแพทย์ธีระเกียรติ เจริญเศรษฐศิลป์รองประธานคณะกรรมการบริหารทุนการศึกษา เครือฯดร.คุณหญิง กษมา วรวรรณ ณ อยุธยากรรมการบริหารทุนการศึกษา เครือฯนายศุภชัย เจียรวนนท์ประธานคณะผู้บริหาร เครือเจริญโภคภัณฑ์ และคณะกรรมการบริห

### Save to CSV

In [115]:
df.to_csv('News_Sanook_5.csv', index=False, encoding ='utf-8-sig')

### or Save to json

In [116]:
df['Release_date'] = (df['Release_date']).astype(str)

In [117]:
df = df.to_dict('records')

In [118]:
import json
with open('News_Sanook_5.json', 'w', encoding ='utf8') as json_file:
    json.dump(df, json_file)

# Upload data to DataPlatform

In [1]:
from dsmlibrary.datanode import DataNode

In [2]:
dir_raw_id = 43

In [2]:
datanode = DataNode()

Init DataNode sucessful!


In [5]:
datanode.upload_file(directory_id=dir_raw_id, file_path='News_Sanook_5.json')

  0%|          | 0.00/2.79M [00:00<?, ?B/s]

{'id': 770,
 'msg': 'file News_Sanook_5.json create sucessful',
 'path': 'thanutchapon/DSI310-02/rawData/News_Sanook_5.json',
 'uploaded': True}

# 02_entiry-extract
* entity extraction from news description using trasnformer Davlan/xlm-roberta-base-ner-hrl

In [ ]:
!pip install transformers torch
!pip install sentencepiece

In [1]:
from dsmlibrary.datanode import DataNode
import json
from tqdm.auto import tqdm
import pandas as pd

In [3]:
dir_raw_id = 43
dir_process_id = 44

In [4]:
meta, fp = datanode.get_file(datanode.get_file_id(directory_id=dir_raw_id, name='News_Sanook_5.json'))
meta

{'owner': 'thanutchapon',
 'human_size': '2.93 MB',
 'name': 'News_Sanook_5.json',
 'description': 'file News_Sanook_5.json',
 'directory': 43,
 'path': 'thanutchapon/DSI310-02/rawData/News_Sanook_5.json'}

In [5]:
data = json.load(fp)
data

[{'Title': '“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย',
  'Release_date': '2022-11-07 18:21',
  'Content': 'รายงานฉบับพิเศษ “ห้องเรียนฟื้นฟูหลังโควิด-19” พบภาวะฉุกเฉินทางการเรียนรู้ของ “เด็กอนุบาล 3 ยุคโควิด-19” ว่าขาดความพร้อมเข้าเรียนในชั้นประถมต้น โดยสะท้อนจากผลวิจัยสถานะความพร้อมในการเข้าสู่ระบบการศึกษาของเด็กปฐมวัย ทั้งด้านทักษะพื้นฐานด้านภาษา ด้านคณิตศาสตร์ และทักษะการรู้คิดเชิงบริหารภาวะการเรียนรู้ถดถอย (Learning Loss) ในปี 2565 เป็นสถานการณ์ที่รุนแรง มีเด็กหางแถวและเกิดความเหลื่อมล้ำมากที่สุด และผู้ปกครองยังอ่านหนังสือให้เด็กฟังน้อยลงในช่วงการระบาดของโรคโควิด-19 เนื่องจากขาดสื่อการเรียนรู้ ส่งผลให้ทักษะการเรียนรู้ของเด็กขาดหายไปกว่าร้อยละ 90เด็กไทย 1 ใน 4 หรือร้อยละ 25 มีพัฒนาการไม่สมวัย โดยพัฒนาการเด็กไม่สมวัยที่พบมากที่สุดคือพัฒนาการด้านการใช้ภาษา ร้อยละ 75.2 รองลงมาคือพัฒนาการด้านการเข้าใจภาษา ร้อยละ 60.1 และพัฒนาการด้านกล้ามเนื้อมัดเล็กและสติปัญญา ร้อยละ 47จากการสังเกตพฤติกรรมของเด็กนักเรียนชั้นประถมศึกษาปีที่ 2 จากห้องเรียน 74 โรงเรียน ในพื้นที่ 6 จังห

In [9]:
# for news_2.parquet
#df2 = pd.read_csv(fp)
#df2

Title      Release_date  \
0    “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
1    “กระทรวงศึกษาธิการ” ปลดล็อกการศึกษาไทย ด้วยนโย...  2022-10-11 17:31   
2    “ภาวะการเรียนรู้ถดถอย” ภัยเงียบที่กำลังกัดเซาะ...  2022-08-26 17:50   
3    ครูจุ๊ย กุลธิดา: เปลือยการศึกษาไทยช่วงวิกฤติโค...  2022-08-04 15:44   
4    2 เยาวชนไทยในโอลิมปิกปรัชญาและเหรียญทองแดงแรกใ...  2022-07-06 16:20   
..                                                 ...               ...   
147        พล.อ.สุรยุทธ์เผย ในหลวงทรงห่วงใยการศึกษาไทย  2013-07-25 13:03   
148            ฮือฮา! เด็ก 2 ขวบ อัจฉริยะภาษา (ชมคลิป)  2013-07-13 13:53   
149          ดุสิตโพลคนฝากรมต.ใหม่เร่งแก้ใต้กระตุ้นศก.  2013-07-05 11:23   
150           Sanook social news วันที่ 5 กรกฎาคม 2556  2013-07-05 10:15   
151              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   

                                               Content  
0    รายงานฉบับพิเศษ “ห้องเรียนฟื้นฟูหลังโควิด-19” ...  
1    การศึกษาของเด็กไทยคือหัวใจสำคัญในการขับเคลื่อน...  
2    บทเรียนงานวิจัยเกี่ยวกับพัฒนาการเด็กปฐมวัย ระบ...  
3    ระบบราชการ ระบบคิดของคนต่อการศึกษา และระบบอำนา...  
4    ชวนรู้จักกับ 2 เยาวชนไทยที่คว้าเหรียญทองแดงและ...  
..                                                 ...  
147  องคมนตรี สุรยุทธ์ เผย พระบาทสมเด็จพระเจ้าอยู่ห...  
148  วันที่ 11 ก.ค. ผู้สื่อข่าวรับแจ้งมีเด็กอัจริยะ...  
149  ดุสิตโพล เผย ประชาชนอยากฝากรัฐมนตรีใหม่ เร่งแก...  
150  คัดเรื่องเด่นประเด็นฮอตในรอบสัปดาห์กับSanook! ...  
151  ปลัดกระทรวงศึกษาธิการ แจง กรรมาธิการงบประมาณปี...  

[152 rows x 3 columns]

In [10]:
#for news_2.parquet
#datanode.write(df=df2, directory=dir_process_id, name="News_Sanook_5", profiling=True, lineage=[datanode.get_file_id(directory_id=dir_raw_id, name='News_Sanook_5.csv')])

{'sucess': True,
 'file_id': 771,
 'path': 'thanutchapon/DSI310-02/processData/News_Sanook_5.parquet',
 'lineage': True}

### NER (NameEntitiesRegcognition)
* extract entity from news description

In [6]:
from transformers import AutoTokenizer, AutoModelForTokenClassification
from transformers import pipeline

In [7]:
tokenizer = AutoTokenizer.from_pretrained("Davlan/xlm-roberta-base-ner-hrl")
model = AutoModelForTokenClassification.from_pretrained("Davlan/xlm-roberta-base-ner-hrl")
nlp = pipeline("ner", model=model, tokenizer=tokenizer)

In [12]:
import re
def post_process(preds):
    data = []
    for i in range(len(preds)): 
        a = preds[i]
        text = a.get('word')
        entity = a.get('entity')
        for j in range(i+1, len(preds)):
            b = preds[j]
            if b.get('start') == a.get('end'):
                text += b.get('word')
                a = b
        if "B-" in entity:  
            data.append({
                'type': entity,
                'text': text
            })
    tmp = []
    for elm in data:
        text = elm.get('text')
        if bool(re.match("[ก-๛]|▁", text)):
            elm.update({'text': text.replace('▁', ' ')})
            tmp.append(elm)
    return tmp

In [13]:
# test
text = data[0]['Content']
text

'รายงานฉบับพิเศษ “ห้องเรียนฟื้นฟูหลังโควิด-19” พบภาวะฉุกเฉินทางการเรียนรู้ของ “เด็กอนุบาล 3 ยุคโควิด-19” ว่าขาดความพร้อมเข้าเรียนในชั้นประถมต้น โดยสะท้อนจากผลวิจัยสถานะความพร้อมในการเข้าสู่ระบบการศึกษาของเด็กปฐมวัย ทั้งด้านทักษะพื้นฐานด้านภาษา ด้านคณิตศาสตร์ และทักษะการรู้คิดเชิงบริหารภาวะการเรียนรู้ถดถอย (Learning Loss) ในปี 2565 เป็นสถานการณ์ที่รุนแรง มีเด็กหางแถวและเกิดความเหลื่อมล้ำมากที่สุด และผู้ปกครองยังอ่านหนังสือให้เด็กฟังน้อยลงในช่วงการระบาดของโรคโควิด-19 เนื่องจากขาดสื่อการเรียนรู้ ส่งผลให้ทักษะการเรียนรู้ของเด็กขาดหายไปกว่าร้อยละ 90เด็กไทย 1 ใน 4 หรือร้อยละ 25 มีพัฒนาการไม่สมวัย โดยพัฒนาการเด็กไม่สมวัยที่พบมากที่สุดคือพัฒนาการด้านการใช้ภาษา ร้อยละ 75.2 รองลงมาคือพัฒนาการด้านการเข้าใจภาษา ร้อยละ 60.1 และพัฒนาการด้านกล้ามเนื้อมัดเล็กและสติปัญญา ร้อยละ 47จากการสังเกตพฤติกรรมของเด็กนักเรียนชั้นประถมศึกษาปีที่ 2 จากห้องเรียน 74 โรงเรียน ในพื้นที่ 6 จังหวัดภาคใต้ พบว่าเด็กนักเรียนจำนวน 98% มีแรงบีบมือต่ำกว่าเกณฑ์เฉลี่ยของเด็กในวัยเดียวกัน โดยมีเด็กนักเรียนที่ผ่านเกณฑ์เพียง 1.19% 

In [14]:
output = nlp(text)
output

[{'entity': 'B-LOC',
  'score': 0.75497895,
  'index': 214,
  'word': 'ภาคใต้',
  'start': 874,
  'end': 880},
 {'entity': 'B-ORG',
  'score': 0.99901295,
  'index': 362,
  'word': 'กองทุน',
  'start': 1453,
  'end': 1459},
 {'entity': 'I-ORG',
  'score': 0.9997131,
  'index': 363,
  'word': 'เพื่อ',
  'start': 1459,
  'end': 1464},
 {'entity': 'I-ORG',
  'score': 0.99974805,
  'index': 364,
  'word': 'ความ',
  'start': 1464,
  'end': 1468},
 {'entity': 'I-ORG',
  'score': 0.99979705,
  'index': 365,
  'word': 'เสมอ',
  'start': 1468,
  'end': 1472},
 {'entity': 'I-ORG',
  'score': 0.99977905,
  'index': 366,
  'word': 'ภาค',
  'start': 1472,
  'end': 1475},
 {'entity': 'I-ORG',
  'score': 0.99966526,
  'index': 367,
  'word': 'ทาง',
  'start': 1475,
  'end': 1478},
 {'entity': 'I-ORG',
  'score': 0.9995227,
  'index': 368,
  'word': 'การศึกษา',
  'start': 1478,
  'end': 1486},
 {'entity': 'B-ORG',
  'score': 0.99944705,
  'index': 370,
  'word': 'ก',
  'start': 1488,
  'end': 1489},
 

In [15]:
import re
post_process(output)

[{'type': 'B-LOC', 'text': 'ภาคใต้'},
 {'type': 'B-ORG', 'text': 'กองทุนเพื่อความเสมอภาคทางการศึกษา'},
 {'type': 'B-ORG', 'text': 'กสศ.'},
 {'type': 'B-ORG',
  'text': 'เครือข่ายโรงเรียนพัฒนาตนเอง มหาวิทยาลัยสงขลานครินทร์'},
 {'type': 'B-LOC', 'text': 'หาดใหญ่'},
 {'type': 'B-ORG', 'text': 'สถาบันวิจัยเพื่อการประเมินและออกแบบนโยบาย'},
 {'type': 'B-ORG', 'text': ' มหาวิทยาลัยหอการค้าไทย'},
 {'type': 'B-ORG', 'text': 'กองทุนเพื่อความเสมอภาคทางการศึกษา'},
 {'type': 'B-ORG', 'text': 'กสศ.'}]

## Process news to spo

In [16]:
spo = []
for news in tqdm(data):
    description = news.get('Content') 
    if description == None:
        continue
    ner = nlp(description)
    processed = post_process(ner)
    for kw in processed:
        spo.append({
            'subject': news.get('Title', ""),
            'release_date': news.get('Release_date', ""),
            'predicate': kw.get('type', ""),
            'object': kw.get('text', "")
        })

  0%|          | 0/152 [00:00<?, ?it/s]

In [17]:
df = pd.DataFrame(spo)
df['predicate'] = df['predicate'].apply(lambda x: x[2:])
df

subject      release_date  \
0     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
1     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
2     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
3     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
4     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
...                                                 ...               ...   
1943              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1944              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1945              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1946              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1947              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   

     predicate                                             object  
0          LOC                                             ภาคใต้  
1          ORG                  กองทุนเพื่อความเสมอภาคทางการศึกษา  
2          ORG                                               กสศ.  
3          ORG  เครือข่ายโรงเรียนพัฒนาตนเอง มหาวิทยาลัยสงขลานค...  
4          LOC                                            หาดใหญ่  
...        ...                                                ...  
1943       ORG                                            กระทรวง  
1944       LOC                                                ไทย  
1945       LOC                                            อาเซียน  
1946       PER                                    อนันต์ ผลอํานวย  
1947       ORG             สํานักงานคณะกรรมการการศึกษาขั้นพื้นฐาน  

[1948 rows x 4 columns]

### write DataNode to DataPlatform

In [18]:
datanode.write(df=df, directory=dir_process_id, name="Analyze_News_5", profiling=True, lineage=[datanode.get_file_id(directory_id=dir_raw_id, name='News_Sanook_5.json')])

File Analyze_News_5.parquet alrady exists, do you want to replace y/n :  y


{'sucess': True,
 'file_id': 772,
 'path': 'thanutchapon/DSI310-02/processData/Analyze_News_5.parquet',
 'lineage': True}

# 03 Graph Visualizaion
* process news SPO analytics via graph algorithm

In [19]:
!pip install networkx

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


### read news SPO from DataPlatform

In [20]:
from dsmlibrary.datanode import DataNode
from tqdm.auto import tqdm

In [21]:
datanode = DataNode()

Init DataNode sucessful!


In [22]:
dir_process_id = 44

In [23]:
df = datanode.read_df(datanode.get_file_id(directory_id=dir_process_id, name="Analyze_News_5.parquet"))
df

subject      release_date  \
0     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
1     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
2     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
3     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
4     “ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแข...  2022-11-07 18:21   
...                                                 ...               ...   
1943              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1944              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1945              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1946              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   
1947              ปลัดศธ.แจงกมธ.งบ57ยันใช้พัฒนาการศึกษา  2013-06-19 13:26   

     predicate                                             object  
0          LOC                                             ภาคใต้  
1          ORG                  กองทุนเพื่อความเสมอภาคทางการศึกษา  
2          ORG                                               กสศ.  
3          ORG  เครือข่ายโรงเรียนพัฒนาตนเอง มหาวิทยาลัยสงขลานค...  
4          LOC                                            หาดใหญ่  
...        ...                                                ...  
1943       ORG                                            กระทรวง  
1944       LOC                                                ไทย  
1945       LOC                                            อาเซียน  
1946       PER                                    อนันต์ ผลอํานวย  
1947       ORG             สํานักงานคณะกรรมการการศึกษาขั้นพื้นฐาน  

[1948 rows x 4 columns]

### prepair graph data

In [24]:
graph_data = [(elm.get('subject'), elm.get('object')) for elm in df.to_dict('records')]
graph_data

[('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย', 'ภาคใต้'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย',
  'กองทุนเพื่อความเสมอภาคทางการศึกษา'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย', 'กสศ.'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย',
  'เครือข่ายโรงเรียนพัฒนาตนเอง มหาวิทยาลัยสงขลานครินทร์'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย', 'หาดใหญ่'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย',
  'สถาบันวิจัยเพื่อการประเมินและออกแบบนโยบาย'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย',
  ' มหาวิทยาลัยหอการค้าไทย'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย',
  'กองทุนเพื่อความเสมอภาคทางการศึกษา'),
 ('“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย', 'กสศ.'),
 ('“กระทรวงศึกษาธิการ” ปลดล็อกการศึกษาไทย ด้วยนโยบาย “ซ่อม สร้าง ป้องกัน”',
  ' กระทรวศึกษาธิการ'),
 ('“กระทรวงศึกษาธิการ” ปลดล็อก

In [25]:
import networkx as nx
import numpy as np
import matplotlib.pyplot as plt

from bokeh.io import output_notebook, show, save
from bokeh.models import Range1d, Circle, ColumnDataSource, MultiLine
from bokeh.plotting import figure
from bokeh.plotting import from_networkx

In [26]:
output_notebook()

Loading BokehJS ...

In [27]:
news_titles = {elm:'name' for elm in list(df['subject'].unique())}
news_titles

{'“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย': 'name',
 '“กระทรวงศึกษาธิการ” ปลดล็อกการศึกษาไทย ด้วยนโยบาย “ซ่อม สร้าง ป้องกัน”': 'name',
 '“ภาวะการเรียนรู้ถดถอย” ภัยเงียบที่กำลังกัดเซาะสังคม': 'name',
 'ครูจุ๊ย กุลธิดา: เปลือยการศึกษาไทยช่วงวิกฤติโควิด-19': 'name',
 '2 เยาวชนไทยในโอลิมปิกปรัชญาและเหรียญทองแดงแรกในประวัติศาสตร์': 'name',
 'นพ.ยงยุทธ วงศ์ภิรมย์ศานติ์: จิตวิทยาว่าด้วย “ความงมงาย” ของคนไทย': 'name',
 'กรุงเทพฯ เมืองหลวงที่มีความเหลื่อมล้ำทางการศึกษาไม่ต่างจากต่างจังหวัด': 'name',
 '"สงกรานต์" ฟาดแรง นักดนตรีซ้อมกันแทบตาย บางคนแค่ไปสันเขื่อน มีงานมีค่าตัวซะแล้ว': 'name',
 'วงการดาราศาสตร์ไทยสูญเสีย วรวิทย์ ตันวุฒิบัณฑิต ปราชญ์ท้องถิ่นนักล่าดาวหาง': 'name',
 '“ครูอัตราจ้าง” ภาพสะท้อนปัญหาการศึกษาไทย': 'name',
 'นายกฯ มอบสาร “พัฒนาครู พัฒนาเด็ก เรียนรู้สู่อนาคต”': 'name',
 'เพื่อไทยชี้ เศรษฐกิจปี 65 "ฟื้นไม่มี หนีไม่พ้น" ยก 8 ปัญหาใหญ่ ที่ไทยต้องเจอ': 'name',
 '“ระบบการศึกษาไทย” มีปัญหาตรงไหนบ้าง': 'name',
 'โฟกัส จีระกุล จี้คนรักเผด็จการ-การศึกษาไทย งดส่

In [28]:
G = nx.Graph(graph_data)
G

In [29]:
node_colors = {elm:'skyblue' if elm in news_titles else 'yellow' for elm in G.nodes()}
node_colors

{'“ภาวะฉุกเฉินทางการเรียนรู้” เมื่อการศึกษาไทยแขวนอยู่บนเส้นด้าย': 'skyblue',
 'ภาคใต้': 'yellow',
 'กองทุนเพื่อความเสมอภาคทางการศึกษา': 'yellow',
 'กสศ.': 'yellow',
 'เครือข่ายโรงเรียนพัฒนาตนเอง มหาวิทยาลัยสงขลานครินทร์': 'yellow',
 'หาดใหญ่': 'yellow',
 'สถาบันวิจัยเพื่อการประเมินและออกแบบนโยบาย': 'yellow',
 ' มหาวิทยาลัยหอการค้าไทย': 'yellow',
 '“กระทรวงศึกษาธิการ” ปลดล็อกการศึกษาไทย ด้วยนโยบาย “ซ่อม สร้าง ป้องกัน”': 'skyblue',
 ' กระทรวศึกษาธิการ': 'yellow',
 'ตรีนุช เทียนทองตรีนุช เทียนทอง': 'yellow',
 'ตรีนุช เทียนทอง': 'yellow',
 'กระทรวงศึกษาธิการ': 'yellow',
 ' ตรีนุช': 'yellow',
 'ตรีนุช': 'yellow',
 '“ภาวะการเรียนรู้ถดถอย” ภัยเงียบที่กำลังกัดเซาะสังคม': 'skyblue',
 'ไทย': 'yellow',
 'วีระชาติ กิเลนทอง': 'yellow',
 'คณะการศึกษาปฐมวัย มหาวิทยาลัยหอการค้าไทย': 'yellow',
 'สถาบันวิจัยเพื่อการพัฒนาและออกแบบนโยบาย': 'yellow',
 'ครูจุ๊ย กุลธิดา: เปลือยการศึกษาไทยช่วงวิกฤติโควิด-19': 'skyblue',
 'ครูจุ๊ย - กุลธิดา รุ่งเรืองเกียรติ': 'yellow',
 'จุ๊ย - กุลธิดา รุ่งเรืองเกียรติ': 'yel

### visualize raw data

In [30]:
title = "News and NameEntities"
HOVER_TOOLTIPS = [("Character", "@index")]
nx.set_node_attributes(G, node_colors, 'node_colors')
plot = figure(tooltips = HOVER_TOOLTIPS,
              tools="pan,wheel_zoom,save,reset,hover", active_scroll='wheel_zoom',
            x_range=Range1d(-10.1, 10.1), y_range=Range1d(-10.1, 10.1), title=title,
              frame_width=1200, frame_height=800
 )

network_graph = from_networkx(G, nx.kamada_kawai_layout, scale=10, center=(0, 0))
network_graph.node_renderer.glyph = Circle(size=15, fill_color='node_colors')
network_graph.edge_renderer.glyph = MultiLine(line_alpha=0.5, line_width=1)
plot.renderers.append(network_graph)
show(plot)

### Compute betweenness_centrality graph

In [31]:
def cal_size(val, k=10, k2=1000):
    val = val * k * k2
    if val > k: 
        return val
    return k

In [32]:
graph_values = nx.centrality.betweenness.betweenness_centrality(G)
node_size = {k:cal_size(v, k=10, k2=1000) for k,v in graph_values.items()}

In [33]:
title = "betweenness_centrality"
HOVER_TOOLTIPS = [("Character", "@index")]

nx.set_node_attributes(G, node_size, 'node_size')
nx.set_node_attributes(G, node_colors, 'node_colors')

plot = figure(tooltips = HOVER_TOOLTIPS,
              tools="pan,wheel_zoom,save,reset,hover", active_scroll='wheel_zoom',
            x_range=Range1d(-10.1, 10.1), y_range=Range1d(-10.1, 10.1), title=title,
              frame_width=1200, frame_height=800
)

network_graph = from_networkx(G, nx.kamada_kawai_layout, scale=10, center=(0, 0))
network_graph.node_renderer.glyph = Circle(fill_color='node_colors', size='node_size')
network_graph.edge_renderer.glyph = MultiLine(line_alpha=0.5, line_width=1)
plot.renderers.append(network_graph)
show(plot)

### compute eigenvector_centrality

In [34]:
graph_values = nx.centrality.eigenvector.eigenvector_centrality(G, max_iter=600)
node_size = {k:cal_size(v, k=10, k2=15) for k,v in graph_values.items()}

In [35]:
title = "xxx"
HOVER_TOOLTIPS = [("Character", "@index")]

nx.set_node_attributes(G, node_size, 'node_size') 
nx.set_node_attributes(G, node_colors, 'node_colors')

plot = figure(tooltips = HOVER_TOOLTIPS,
              tools="pan,wheel_zoom,save,reset,hover", active_scroll='wheel_zoom',
            x_range=Range1d(-10.1, 10.1), y_range=Range1d(-10.1, 10.1), title=title,
              frame_width=1200, frame_height=800
)

network_graph = from_networkx(G, nx.kamada_kawai_layout, scale=10, center=(0, 0))
network_graph.node_renderer.glyph = Circle(fill_color='node_colors', size='node_size')
network_graph.edge_renderer.glyph = MultiLine(line_alpha=0.5, line_width=1)
plot.renderers.append(network_graph)
show(plot)